In [1]:
import ast
import csv
import json

import numpy as np
import pandas as pd

import requests

pd.set_option('display.max_columns', None)

## Loading datasets

In [2]:
roar_df = pd.read_csv('../data/raw/export_roar_CSV.csv', dtype='str')
roar_df.head()

eprintid rev_number eprint_status userid importid source                dir  \
0      921        517       archive      1      NaN    NaN  disk0/00/00/09/21   
1     1489        556       archive      1      NaN    NaN  disk0/00/00/14/89   
2      606        657       archive      1      NaN    NaN  disk0/00/00/06/06   
3      606        NaN           NaN    NaN      NaN    NaN                NaN   
4      606        NaN           NaN    NaN      NaN    NaN                NaN   

             datestamp              lastmod       status_changed     type  \
0  2010-01-06 13:44:55  2016-04-17 21:54:11  2010-01-06 13:44:55   theses   
1  2010-01-06 13:46:05  2016-04-17 21:49:00  2010-01-06 13:46:05    other   
2  2010-01-06 13:44:31  2016-04-17 21:53:14  2010-01-06 13:44:31  subject   
3                  NaN                  NaN                  NaN      NaN   
4                  NaN                  NaN                  NaN      NaN   

  succeeds commentary metadata_visibility latitude longitude relation_type  \
0      NaN        NaN                show      NaN       NaN           NaN   
1      NaN        NaN                show      NaN       NaN           NaN   
2      NaN        NaN                show      NaN       NaN           NaN   
3      NaN        NaN                 NaN      NaN       NaN           NaN   
4      NaN        NaN                 NaN      NaN       NaN           NaN   

  relation_uri item_issues_id item_issues_type item_issues_description  \
0          NaN            NaN              NaN                     NaN   
1          NaN            NaN              NaN                     NaN   
2          NaN            NaN              NaN                     NaN   
3          NaN            NaN              NaN                     NaN   
4          NaN            NaN              NaN                     NaN   

  item_issues_timestamp item_issues_status item_issues_reported_by  \
0                   NaN                NaN                     NaN   
1                   NaN                NaN                     NaN   
2                   NaN                NaN                     NaN   
3                   NaN                NaN                     NaN   
4                   NaN                NaN                     NaN   

  item_issues_resolved_by item_issues_comment item_issues_count  \
0                     NaN                 NaN                 0   
1                     NaN                 NaN                 0   
2                     NaN                 NaN                 0   
3                     NaN                 NaN               NaN   
4                     NaN                 NaN               NaN   

  sword_depositor sword_slug exemplar  \
0             NaN        NaN    FALSE   
1             NaN        NaN      NaN   
2             NaN        NaN      NaN   
3             NaN        NaN      NaN   
4             NaN        NaN      NaN   

                                           home_page  \
0             http://alcme.oclc.org/ndltd/index.html   
1  http://prensahistorica.mcu.es/prensahistorica/...   
2                   http://hal.archives-ouvertes.fr/   
3                                                NaN   
4                                                NaN   

                                               title  \
0  Networked Digital Library of Theses and Disser...   
1                Virtual Library of Historical Press   
2                        HAL: Hyper Article en Ligne   
3                                                NaN   
4                                                NaN   

                                             oai_pmh sword_endpoint rss_feed  \
0     http://alcme.oclc.org/ndltd/servlet/OAIHandler            NaN      NaN   
1  http://prensahistorica.mcu.es/prensahistorica/...            NaN      NaN   
2        http://hal.archives-ouvertes.fr/oai/oai.php            NaN      NaN   
3                                                NaN            NaN      

In [3]:
roar_df.columns

Index(['eprintid', 'rev_number', 'eprint_status', 'userid', 'importid',
       'source', 'dir', 'datestamp', 'lastmod', 'status_changed', 'type',
       'succeeds', 'commentary', 'metadata_visibility', 'latitude',
       'longitude', 'relation_type', 'relation_uri', 'item_issues_id',
       'item_issues_type', 'item_issues_description', 'item_issues_timestamp',
       'item_issues_status', 'item_issues_reported_by',
       'item_issues_resolved_by', 'item_issues_comment', 'item_issues_count',
       'sword_depositor', 'sword_slug', 'exemplar', 'home_page', 'title',
       'oai_pmh', 'sword_endpoint', 'rss_feed', 'twitter_feed', 'description',
       'fulltext', 'open_access', 'mandate', 'organisation_title',
       'organisation_home_page', 'location_country', 'location_city',
       'location_latitude', 'location_longitude', 'software', 'geoname',
       'version', 'subjects', 'date', 'note', 'suggestions', 'activity_low',
       'activity_medium', 'activity_high', 'recordcount', 'rec

In [4]:
roar_df.describe(include='all')

eprintid rev_number eprint_status userid importid source  \
count     18079       5444          5444   5444        0      0   
unique     5444        660             1   2189        0      0   
top       12118         11       archive      1      NaN    NaN   
freq        238        333          5444   1330      NaN    NaN   

                      dir            datestamp              lastmod  \
count                5444                 5444                 5444   
unique               5444                 4198                 4043   
top     disk0/00/00/09/21  2010-01-06 13:43:48  2016-04-17 21:55:19   
freq                    1                   16                    8   

             status_changed           type succeeds commentary  \
count                  5444           5444      108          0   
unique                 4230             12      108          0   
top     2010-01-06 13:43:48  institutional     3164        NaN   
freq                     16           3853        1        NaN   

       metadata_visibility latitude longitude relation_type relation_uri  \
count                 5444        0         0             0            0   
unique                   2        0         0             0            0   
top                   show      NaN       NaN           NaN          NaN   
freq                  5402      NaN       NaN           NaN          NaN   

           item_issues_id item_issues_type  \
count                  86               86   
unique                 51                3   
top     bad_oai_pmh_url_0  duplicate_title   
freq                   18               47   

                                  item_issues_description  \
count                                                  86   
unique                                                 68   
top     Similar title to <xhtml:table xmlns:xhtml="htt...   
freq                                                    3   

       item_issues_timestamp item_issues_status item_issues_reported_by  \
count                     86                 86                       0   
unique                     3                  2                       0   
top      2010-01-13 10:44:49         discovered                     NaN   
freq                      68                 53                     NaN   

       item_issues_resolved_by item_issues_comment item_issues_count  \
count                        0                   0              2242   
unique                       0                   0                 4   
top                        NaN                 NaN                 0   
freq                       NaN                 NaN              2201   

       sword_depositor sword_slug exemplar                       home_page  \
count                0          0      268                            5437   
unique               0          0        2                            5271   
top                NaN        NaN    FALSE  http://eprints.upnjatim.ac.id/   
freq               NaN        NaN      261                               4   

                            title                                 oai_pmh  \
count                        5442                                    4567   
unique                       5143                                    4278   
top     Repositorio Institucional  http://virtuelcampus.univ-msila.dz/fll   
freq                            7                                       5   

                                      sword_endpoint  \
count                                            178   
unique                                           172   
top     http://producao.usp.br/sword/servicedocument   
freq                                               2   

                                                 rss_feed  \
count                                                1538   
unique                                               1485   
top     http://eprints.upnjatim.ac.id/cgi/latest_tool?...   
freq                       

In [5]:
roar_df[roar_df.eprintid == '606']

eprintid rev_number eprint_status userid importid source                dir  \
2      606        657       archive      1      NaN    NaN  disk0/00/00/06/06   
3      606        NaN           NaN    NaN      NaN    NaN                NaN   
4      606        NaN           NaN    NaN      NaN    NaN                NaN   

             datestamp              lastmod       status_changed     type  \
2  2010-01-06 13:44:31  2016-04-17 21:53:14  2010-01-06 13:44:31  subject   
3                  NaN                  NaN                  NaN      NaN   
4                  NaN                  NaN                  NaN      NaN   

  succeeds commentary metadata_visibility latitude longitude relation_type  \
2      NaN        NaN                show      NaN       NaN           NaN   
3      NaN        NaN                 NaN      NaN       NaN           NaN   
4      NaN        NaN                 NaN      NaN       NaN           NaN   

  relation_uri item_issues_id item_issues_type item_issues_description  \
2          NaN            NaN              NaN                     NaN   
3          NaN            NaN              NaN                     NaN   
4          NaN            NaN              NaN                     NaN   

  item_issues_timestamp item_issues_status item_issues_reported_by  \
2                   NaN                NaN                     NaN   
3                   NaN                NaN                     NaN   
4                   NaN                NaN                     NaN   

  item_issues_resolved_by item_issues_comment item_issues_count  \
2                     NaN                 NaN                 0   
3                     NaN                 NaN               NaN   
4                     NaN                 NaN               NaN   

  sword_depositor sword_slug exemplar                         home_page  \
2             NaN        NaN      NaN  http://hal.archives-ouvertes.fr/   
3             NaN        NaN      NaN                               NaN   
4             NaN        NaN      NaN                               NaN   

                         title                                      oai_pmh  \
2  HAL: Hyper Article en Ligne  http://hal.archives-ouvertes.fr/oai/oai.php   
3                          NaN                                          NaN   
4                          NaN                                          NaN   

  sword_endpoint rss_feed twitter_feed description fulltext open_access  \
2            NaN      NaN          NaN         NaN     TRUE        TRUE   
3            NaN      NaN          NaN         NaN      NaN         NaN   
4            NaN      NaN          NaN         NaN      NaN         NaN   

  mandate organisation_title organisation_home_page location_country  \
2     NaN                NaN                    NaN               fr   
3     NaN                NaN                    NaN              NaN   
4     NaN                NaN                    NaN              NaN   

  location_city location_latitude location_longitude software       geoname  \
2           NaN               NaN                NaN      hal  geoname_2_FR   
3           NaN               NaN                NaN      NaN           NaN   
4           NaN               NaN                NaN      NaN           NaN   

  version subjects                 date note suggestions activity_low  \
2   other      NaN  1998-11-02 11:53:57  NaN         NaN            0   
3     NaN      NaN                  NaN  NaN         NaN          NaN   
4     NaN      NaN                  NaN  NaN         NaN          NaN   

  activity_medium activity_high recordcount  \
2               0             2      675816   
3             NaN           NaN         NaN   
4             NaN           NaN         NaN   

                                       recordhistory fulltexts_total  \
2  4,12,17,26,43,57,81,185,431,861,1184,1517,2442...             NaN   
3                                                NaN     

In [6]:
roar_df = roar_df.groupby('eprintid').aggregate(set)
roar_df.head()

rev_number   eprint_status     userid importid source  \
eprintid                                                          
1         {633, nan}  {nan, archive}   {nan, 1}    {nan}  {nan}   
10        {nan, 511}  {nan, archive}   {nan, 1}    {nan}  {nan}   
1000           {274}       {archive}        {1}    {nan}  {nan}   
10001      {nan, 20}  {nan, archive}  {nan, 91}    {nan}  {nan}   
10008           {11}       {archive}      {404}    {nan}  {nan}   

                               dir                   datestamp  \
eprintid                                                         
1         {nan, disk0/00/00/00/01}  {nan, 2010-01-06 13:43:48}   
10        {nan, disk0/00/00/00/10}  {nan, 2010-01-06 13:43:48}   
1000           {disk0/00/00/10/00}       {2010-01-06 13:45:01}   
10001     {nan, disk0/00/01/00/01}  {nan, 2015-08-08 14:52:11}   
10008          {disk0/00/01/00/08}       {2015-08-08 14:52:26}   

                             lastmod              status_changed  \
eprintid                                                           
1         {nan, 2011-07-18 05:40:07}  {nan, 2010-01-06 13:43:48}   
10        {nan, 2011-07-18 05:40:13}  {nan, 2010-01-06 13:43:48}   
1000           {2011-07-06 08:21:21}       {2010-01-06 13:45:01}   
10001     {nan, 2016-03-21 19:44:01}  {nan, 2015-08-08 14:52:11}   
10008          {2016-03-21 19:43:51}       {2015-08-08 14:52:26}   

                          type succeeds commentary metadata_visibility  \
eprintid                                                                 
1               {nan, subject}    {nan}      {nan}         {show, nan}   
10        {nan, institutional}    {nan}      {nan}         {show, nan}   
1000                 {subject}    {nan}      {nan}              {show}   
10001           {nan, subject}    {nan}      {nan}         {show, nan}   
10008          {institutional}    {nan}      {nan}              {show}   

         latitude longitude relation_type relation_uri item_issues_id  \
eprintid                                                                
1           {nan}     {nan}         {nan}        {nan}          {nan}   
10          {nan}     {nan}         {nan}        {nan}          {nan}   
1000        {nan}     {nan}         {nan}        {nan}          {nan}   
10001       {nan}     {nan}         {nan}        {nan}          {nan}   
10008       {nan}     {nan}         {nan}        {nan}          {nan}   

         item_issues_type item_issues_description item_issues_timestamp  \
eprintid                                                                  
1                   {nan}                   {nan}                 {nan}   
10                  {nan}                   {nan}                 {nan}   
1000                {nan}                   {nan}                 {nan}   
10001               {nan}                   {nan}                 {nan}   
10008               {nan}                   {nan}                 {nan}   

         item_issues_status item_issues_reported_by item_issues_resolved_by  \
eprintid                                                                      
1                     {nan}                   {nan}                   {nan}   
10                    {nan}                   {nan}                   {nan}   
1000                  {nan}                   {nan}                   {nan}   
10001                 {nan}                   {nan}                   {nan}   
10008                 {nan}                   {nan}                   {nan}   

         item_issues_comment item_issues_count sword_depositor sword_slug  \
eprintid                                                                    
1                      {nan}          {nan, 0}           {nan}      {nan}   
10                     {nan}          {nan, 0}           {nan}      {nan}   
1000                   {nan}               {0}           {nan}      {nan}   
10001                  {nan}             {nan}           {nan}      {nan}   
10008                  {nan

In [7]:
def value_or_list(cell_set):
    copy = set(cell_set)
    copy.discard(np.nan) 
    if len(copy) == 0:
        return np.nan
    if len(copy) == 1:
        return copy.pop()
    return list(copy)
        
roar_df = roar_df.applymap(value_or_list)
roar_df.head()

rev_number eprint_status userid  importid  source                dir  \
eprintid                                                                        
1               633       archive      1       NaN     NaN  disk0/00/00/00/01   
10              511       archive      1       NaN     NaN  disk0/00/00/00/10   
1000            274       archive      1       NaN     NaN  disk0/00/00/10/00   
10001            20       archive     91       NaN     NaN  disk0/00/01/00/01   
10008            11       archive    404       NaN     NaN  disk0/00/01/00/08   

                    datestamp              lastmod       status_changed  \
eprintid                                                                  
1         2010-01-06 13:43:48  2011-07-18 05:40:07  2010-01-06 13:43:48   
10        2010-01-06 13:43:48  2011-07-18 05:40:13  2010-01-06 13:43:48   
1000      2010-01-06 13:45:01  2011-07-06 08:21:21  2010-01-06 13:45:01   
10001     2015-08-08 14:52:11  2016-03-21 19:44:01  2015-08-08 14:52:11   
10008     2015-08-08 14:52:26  2016-03-21 19:43:51  2015-08-08 14:52:26   

                   type succeeds  commentary metadata_visibility  latitude  \
eprintid                                                                     
1               subject      NaN         NaN                show       NaN   
10        institutional      NaN         NaN                show       NaN   
1000            subject      NaN         NaN                show       NaN   
10001           subject      NaN         NaN                show       NaN   
10008     institutional      NaN         NaN                show       NaN   

          longitude  relation_type  relation_uri item_issues_id  \
eprintid                                                          
1               NaN            NaN           NaN            NaN   
10              NaN            NaN           NaN            NaN   
1000            NaN            NaN           NaN            NaN   
10001           NaN            NaN           NaN            NaN   
10008           NaN            NaN           NaN            NaN   

         item_issues_type item_issues_description item_issues_timestamp  \
eprintid                                                                  
1                     NaN                     NaN                   NaN   
10                    NaN                     NaN                   NaN   
1000                  NaN                     NaN                   NaN   
10001                 NaN                     NaN                   NaN   
10008                 NaN                     NaN                   NaN   

         item_issues_status  item_issues_reported_by  item_issues_resolved_by  \
eprintid                                                                        
1                       NaN                      NaN                      NaN   
10                      NaN                      NaN                      NaN   
1000                    NaN                      NaN                      NaN   
10001                   NaN                      NaN                      NaN   
10008                   NaN                      NaN                      NaN   

          item_issues_comment item_issues_count  sword_depositor  sword_slug  \
eprintid                                                                       
1                         NaN                 0              NaN         NaN   
10                        NaN                 0              NaN         NaN   
1000                      NaN                 0              NaN         NaN   
10001                     NaN               NaN              NaN         NaN   
10008                     NaN               NaN              NaN         NaN   

         exemplar                                    home_page  \
eprintid                                                         
1             NaN              http://archivesic.ccsd.cnrs.fr/   
10            NaN              http://www.div

In [8]:
roar_df.reset_index(inplace=True)
roar_df[roar_df.eprintid == '606']

eprintid rev_number eprint_status userid  importid  source  \
4259      606        657       archive      1       NaN     NaN   

                    dir            datestamp              lastmod  \
4259  disk0/00/00/06/06  2010-01-06 13:44:31  2016-04-17 21:53:14   

           status_changed     type succeeds  commentary metadata_visibility  \
4259  2010-01-06 13:44:31  subject      NaN         NaN                show   

      latitude  longitude  relation_type  relation_uri item_issues_id  \
4259       NaN        NaN            NaN           NaN            NaN   

     item_issues_type item_issues_description item_issues_timestamp  \
4259              NaN                     NaN                   NaN   

     item_issues_status  item_issues_reported_by  item_issues_resolved_by  \
4259                NaN                      NaN                      NaN   

      item_issues_comment item_issues_count  sword_depositor  sword_slug  \
4259                  NaN                 0              NaN         NaN   

     exemplar                         home_page                        title  \
4259      NaN  http://hal.archives-ouvertes.fr/  HAL: Hyper Article en Ligne   

                                          oai_pmh sword_endpoint rss_feed  \
4259  http://hal.archives-ouvertes.fr/oai/oai.php            NaN      NaN   

     twitter_feed description fulltext open_access mandate organisation_title  \
4259          NaN         NaN     TRUE        TRUE     NaN                NaN   

     organisation_home_page location_country location_city location_latitude  \
4259                    NaN               fr           NaN               NaN   

     location_longitude software       geoname version subjects  \
4259                NaN      hal  geoname_2_FR   other      NaN   

                     date note suggestions activity_low activity_medium  \
4259  1998-11-02 11:53:57  NaN         NaN            0               0   

     activity_high recordcount  \
4259             2      675816   

                                          recordhistory fulltexts_total  \
4259  4,12,17,26,43,57,81,185,431,861,1184,1517,2442...             NaN   

     fulltexts_docs fulltexts_rtotal fulltexts_rdocs  \
4259            NaN              NaN             NaN   

                       registry_name      registry_id submit_to  \
4259  [celestial, opendoar, roarmap]  [69, 1106, 166]       NaN   

     submitted_to_name submitted_to_done webometrics_rank webometrics_size  \
4259               NaN               NaN                1                6   

     webometrics_visibility webometrics_rich_files webometrics_scholar  \
4259                      1                      1                   1   

                                       monthly_deposits total_deposits  \
4259  0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,...           3063   

     association  
4259         NaN

In [9]:
roar_df.describe(include='all')

eprintid rev_number eprint_status userid  importid  source  \
count      5444       5444          5444   5444       0.0     0.0   
unique     5444        660             1   2189       NaN     NaN   
top           1         11       archive      1       NaN     NaN   
freq          1        333          5444   1330       NaN     NaN   
mean        NaN        NaN           NaN    NaN       NaN     NaN   
std         NaN        NaN           NaN    NaN       NaN     NaN   
min         NaN        NaN           NaN    NaN       NaN     NaN   
25%         NaN        NaN           NaN    NaN       NaN     NaN   
50%         NaN        NaN           NaN    NaN       NaN     NaN   
75%         NaN        NaN           NaN    NaN       NaN     NaN   
max         NaN        NaN           NaN    NaN       NaN     NaN   

                      dir            datestamp              lastmod  \
count                5444                 5444                 5444   
unique               5444                 4198                 4043   
top     disk0/00/00/00/01  2010-01-06 13:43:48  2011-07-06 08:24:53   
freq                    1                   16                    8   
mean                  NaN                  NaN                  NaN   
std                   NaN                  NaN                  NaN   
min                   NaN                  NaN                  NaN   
25%                   NaN                  NaN                  NaN   
50%                   NaN                  NaN                  NaN   
75%                   NaN                  NaN                  NaN   
max                   NaN                  NaN                  NaN   

             status_changed           type succeeds  commentary  \
count                  5444           5444      108         0.0   
unique                 4230             12      108         NaN   
top     2010-01-06 13:43:48  institutional    10164         NaN   
freq                     16           3853        1         NaN   
mean                    NaN            NaN      NaN         NaN   
std                     NaN            NaN      NaN         NaN   
min                     NaN            NaN      NaN         NaN   
25%                     NaN            NaN      NaN         NaN   
50%                     NaN            NaN      NaN         NaN   
75%                     NaN            NaN      NaN         NaN   
max                     NaN            NaN      NaN         NaN   

       metadata_visibility  latitude  longitude  relation_type  relation_uri  \
count                 5444       0.0        0.0            0.0           0.0   
unique                   2       NaN        NaN            NaN           NaN   
top                   show       NaN        NaN            NaN           NaN   
freq                  5402       NaN        NaN            NaN           NaN   
mean                   NaN       NaN        NaN            NaN           NaN   
std                    NaN       NaN        NaN            NaN           NaN   
min                    NaN       NaN        NaN            NaN           NaN   
25%                    NaN       NaN        NaN            NaN           NaN   
50%                    NaN       NaN        NaN            NaN           NaN   
75%                    NaN       NaN        NaN            NaN           NaN   
max                    NaN       NaN        NaN            NaN           NaN   

           item_issues_id item_issues_type  \
count                  63               63   
unique                 48                5   
top     bad_oai_pmh_url_0  duplicate_title   
freq                   15               33   
mean                  NaN              NaN   
std                   NaN              NaN   
min                   NaN              NaN   
25%                   NaN              NaN   
50%                   NaN              NaN   
75%                   NaN              NaN   
max                   NaN              NaN   

      

In [10]:
roar_df.isna().sum()[:40]

eprintid                      0
rev_number                    0
eprint_status                 0
userid                        0
importid                   5444
source                     5444
dir                           0
datestamp                     0
lastmod                       0
status_changed                0
type                          0
succeeds                   5336
commentary                 5444
metadata_visibility           0
latitude                   5444
longitude                  5444
relation_type              5444
relation_uri               5444
item_issues_id             5381
item_issues_type           5381
item_issues_description    5381
item_issues_timestamp      5381
item_issues_status         5381
item_issues_reported_by    5444
item_issues_resolved_by    5444
item_issues_comment        5444
item_issues_count          3202
sword_depositor            5444
sword_slug                 5444
exemplar                   5176
home_page                     7
title   

In [11]:
roar_df.isna().sum()[40:]

organisation_title         984
organisation_home_page    1158
location_country           306
location_city             1730
location_latitude         1719
location_longitude        1736
software                   744
geoname                    714
version                      0
subjects                  4155
date                        15
note                      5226
suggestions               5255
activity_low              3156
activity_medium           3156
activity_high             3156
recordcount               3154
recordhistory             3156
fulltexts_total           5174
fulltexts_docs            5186
fulltexts_rtotal          5174
fulltexts_rdocs           5186
registry_name              839
registry_id                864
submit_to                 5069
submitted_to_name         5239
submitted_to_done         5239
webometrics_rank          5296
webometrics_size          5296
webometrics_visibility    5296
webometrics_rich_files    5296
webometrics_scholar       5296
monthly_

In [12]:
pd.DataFrame(roar_df.type).groupby('type').size()

type
database            74
demonstration       20
institutional     3853
journal            125
learning            77
multi              143
opendata            41
other              410
researchdata        55
subject            295
theses             349
webobservatory       2
dtype: int64

In [13]:
pd.DataFrame(roar_df.open_access).groupby('open_access').size()

open_access
FALSE    1501
TRUE     2696
dtype: int64

In [14]:
pd.DataFrame(roar_df.mandate).groupby('mandate').size()

mandate
FALSE    2748
TRUE      998
dtype: int64